# Bibliography Categorization: 'BibCat'
## Tutorial: Estimating performance of classifiers in bibcat.



---


## Introduction.

In this tutorial, we will use bibcat to estimate the performance of classifiers on sets of texts.


---

## User Workflow: Training a machine learning (ML) model.


The `Performance` class contains user-friendly methods for estimating the performance of given classifiers and outputting that performance as, e.g., confusion matrices.  We overview how this method can be run in the code blocks below.

For this tutorial, we assume that the user has already run the trainML tutorial, and so has generated and saved a machine learning model.

In [1]:
#Import external packages
import re
import os
import sys
import json
import numpy as np


In [2]:
# Set up for fetching necessary bibcat modules for the tutorial
# Check work directories: src/ is where all source python scripts are available. 
current_dir= os.path.dirname(os.path.abspath('__file__'))
_parent = os.path.dirname(current_dir)
src_dir = os.path.join(_parent, "src")

print(f'Current Directory: {current_dir}')
print(f'Source directory: {src_dir}')

# move to the ../src/ directory to import necessary modules. 
os.chdir(src_dir)

Current Directory: /Users/jamila.pegues/Documents/STScI_Fellowship/Functional/Library/BibTracking/repo_stsci/bibcat/docs
Source directory: /Users/jamila.pegues/Documents/STScI_Fellowship/Functional/Library/BibTracking/repo_stsci/bibcat/src


In [3]:
#Import bibcat packages
import bibcat_classes as bibcat
import bibcat_config as config
import bibcat_parameters as params #Temporary file until contents moved elsewhere

Root directory =/Users/jamila.pegues/Documents/STScI_Fellowship/Functional/Library/BibTracking/repo_stsci/bibcat/src, parent directory=/Users/jamila.pegues/Documents/STScI_Fellowship/Functional/Library/BibTracking/repo_stsci/bibcat
/Users/jamila.pegues/Documents/STScI_Fellowship/Functional/Library/BibTracking/repo_stsci/bibcat/src/models folder already exists.
/Users/jamila.pegues/Documents/STScI_Fellowship/Functional/Library/BibTracking/repo_stsci/bibcat/output folder already exists.


In [4]:
#Set parameters for each operator and its internal classifier
#Global parameters
do_verify_truematch = True #A very important parameter - discuss with J.P. first!!!  Set it to either True or False.
do_raise_innererror = False #If True, will stop if exception encountered; if False, will print error and continue
do_reuse_run = True
list_threshold_arrays = [np.linspace(0.5, 0.95, 20)]*2 #For uncertainty test
class_mapper = params.map_papertypes #Mapper for class types; None for no mapper

#For operator 1
mapper_1 = class_mapper #Mapper to mask classifications; None if no masking
threshold_1 = 0.70 #Uncertainty threshold for this classifier
buffer_1 = 0

#For operator 2
mapper_2 = class_mapper #Mapper to mask classifications; None if no masking
threshold_2 = 0.70 #Uncertainty threshold for this classifier
buffer_2 = 0

#Gather parameters into lists
list_mappers = [mapper_1, mapper_2]
list_thresholds = [threshold_1, threshold_2]
list_buffers = [buffer_1, buffer_2]

In [5]:
#Set some overarching global variables
seed_test = 20 #Random seed for shuffling text dataset
np.random.seed(seed_test)
do_shuffle = True #Whether or not to shuffle the text dataset
do_real_testdata = True #If True, will use real papers to test performance; if False, will use fake texts below
#
max_tests = None #100 #Number of text entries to test the performance for; None for all tests available
mode_modif = "none" #"skim_anon" #"skim_trim_anon" #None #We are using preprocessed data in this tutorial, so we do not need a processing mode at all
#
#Prepare some Keyword objects
all_kobjs = params.all_kobjs

In [6]:
#Fetch filepaths for model and data
name_model = config.name_model
filepath_json = config.path_json
dir_model = os.path.join(config.dir_allmodels, name_model)
#
#Set and create (as needed) directories for storing performance output
filepath_output = os.path.join(dir_model, "output") #Where to store performance output, such as confusion matrices
if (not os.path.exists(filepath_output)):
    os.makedirs(filepath_output)
    print("Output folder created at: {0}".format(filepath_output))
print("Output will be saved to: {0}".format(filepath_output))
#
#Set directories for fetching text
dir_info = dir_model
folder_test = config.folders_TVT["test"]
dir_test = os.path.join(dir_model, folder_test)

Output folder created at: /Users/jamila.pegues/Documents/STScI_Fellowship/Functional/Library/BibTracking/repo_stsci/bibcat/src/models/run_class2_full_none_uniform/output
Output will be saved to: /Users/jamila.pegues/Documents/STScI_Fellowship/Functional/Library/BibTracking/repo_stsci/bibcat/src/models/run_class2_full_none_uniform/output


Let's build a set of classifiers for which we'd like to test the performance.  We'll then feed each of those classifiers into an instance of the Operator class to handle them.

In [7]:
#Create a list of classifiers
#This can be modified to use whatever classifiers you'd like.
#Load a previously trained ML model
filepath_model = os.path.join(dir_model, (name_model+".npy"))
fileloc_ML = os.path.join(dir_model, (config.tfoutput_prefix+name_model))
classifier_ML = bibcat.Classifier_ML(filepath_model=filepath_model, fileloc_ML=fileloc_ML, do_verbose=True)
#

#Load a rule-based classifier
classifier_rules = bibcat.Classifier_Rules()
#

INFO:absl:using Lamb optimizer


In [8]:
#Load models into instances of the Operator class
operator_1 = bibcat.Operator(classifier=classifier_ML, mode=mode_modif, keyword_objs=all_kobjs,
                            name="Operator_ML", do_verbose=True, load_check_truematch=True, do_verbose_deep=False)
operator_2 = bibcat.Operator(classifier=classifier_rules,
                            name="Operator_RB", mode=mode_modif, keyword_objs=all_kobjs,
                            do_verbose=True, do_verbose_deep=False)
list_operators = [operator_1, operator_2] #Feel free to add more/less operators here.
#

Instance of Operator successfully initialized!
Keyword objects:
0: Keyword Object:
Name: Hubble
Keywords: ['Hubble Space Telescope', 'Hubble Telescope', 'Hubble']
Acronyms: ['HST', 'HT']
Banned Overlap: ['Hubble Legacy Archive']

1: Keyword Object:
Name: Webb Telescope
Keywords: ['James Webb Space Telescope', 'Webb Space Telescope', 'James Webb Telescope', 'Webb Telescope']
Acronyms: ['JWST', 'JST', 'JT']
Banned Overlap: []

2: Keyword Object:
Name: Transiting Exoplanet Survey Satellite
Keywords: ['Transiting Exoplanet Survey Satellite']
Acronyms: ['TESS']
Banned Overlap: []

3: Keyword Object:
Name: Kepler
Keywords: ['Kepler']
Acronyms: []
Banned Overlap: []

4: Keyword Object:
Name: Pan-STARRS
Keywords: ['Panoramic Survey Telescope and Rapid Response System', 'Pan-STARRS1', 'Pan-STARRS']
Acronyms: ['PanSTARRS1', 'PanSTARRS', 'PS1']
Banned Overlap: []

5: Keyword Object:
Name: Galaxy Evolution Explorer
Keywords: ['Galaxy Evolution Explorer']
Acronyms: ['GALEX']
Banned Overlap: []

6: 

Now, let's fetch some text for our classifiers to classify. For this tutorial, we'll load previously processed texts from the directory containing the test set for the ML classifier.

In [9]:
#For use of real papers from test dataset to test on
if (do_real_testdata):
    #Load information for processed bibcodes reserved for testing
    dict_TVTinfo = np.load(os.path.join(dir_info, "dict_TVTinfo.npy"), allow_pickle=True).item()
    list_test_bibcodes = [key for key in dict_TVTinfo if (dict_TVTinfo[key]["folder_TVT"] == folder_test)]
    
    #Load the original data
    with open(filepath_json, 'r') as openfile:
        dataset = json.load(openfile)
    #
    
    #Extract text information for the bibcodes reserved for testing
    list_test_indanddata_raw = [(ii, dataset[ii]) for ii in range(0, len(dataset))
                                if (dataset[ii]["bibcode"] in list_test_bibcodes)] #Data for test set
    #
    
    #Shuffle, if requested
    if do_shuffle:
        np.random.shuffle(list_test_indanddata_raw)
    #
    
    #Extract target number of test papers from the test bibcodes
    if (max_tests is not None): #Fetch subset of tests
        list_test_indanddata = list_test_indanddata_raw[0:max_tests]
    else: #Use all tests
        list_test_indanddata = list_test_indanddata_raw
    #
    
    #Process the text input into dictionary format for inputting into the codebase
    dict_texts = {} #To hold formatted text entries
    for ii in range(0, len(list_test_indanddata)):
        curr_ind = list_test_indanddata[ii][0]
        curr_data = list_test_indanddata[ii][1]
        #
        #Convert this data entry into dictionary with: key:text,id,bibcode,mission structure
        curr_info = {"text":curr_data["body"], "id":str(curr_ind), "bibcode":curr_data["bibcode"],
                    "missions":{}}
        for curr_mission in curr_data["class_missions"]: #Iterate through missions for this paper
            for curr_kobj in all_kobjs: #Iterate through declared Keyword objects
                curr_name = curr_kobj.get_name()
                #Store mission data under keyword name, if applicable
                if (curr_kobj.is_keyword(curr_mission)):
                    curr_info["missions"][curr_name] = {"mission":curr_name,
                                                    "class":curr_data["class_missions"][curr_mission]["papertype"]}
                #
                #Otherwise, store that this mission was not detected for this text
                else:
                    curr_info["missions"][curr_name] = {"mission":curr_name, "class":config.verdict_rejection}                    
            #
        #
        #Store this data entry
        dict_texts[str(curr_ind)] = curr_info
    #
    
    #Print some notes about the testing data
    print("Number of texts in text set: {0}".format(len(dict_texts)))
    print("")
    for key in dict_texts:
        print("Entry {0}:".format(key))
        print("ID: {0}".format(dict_texts[key]["id"]))
        print("Bibcode: {0}".format(dict_texts[key]["bibcode"]))
        print("Missions: {0}".format(dict_texts[key]["missions"]))
        print("Start of text:\n{0}".format(dict_texts[key]["text"][0:500]))
        print("-\n")
    #
#

Number of texts in text set: 4632

Entry 42775:
ID: 42775
Bibcode: 2018Icar..313...93K
Missions: {'Hubble': {'mission': 'Hubble', 'class': 'MENTION'}, 'Webb Telescope': {'mission': 'Webb Telescope', 'class': 'z_notmatch'}, 'Transiting Exoplanet Survey Satellite': {'mission': 'Transiting Exoplanet Survey Satellite', 'class': 'z_notmatch'}, 'Kepler': {'mission': 'Kepler', 'class': 'z_notmatch'}, 'Pan-STARRS': {'mission': 'Pan-STARRS', 'class': 'z_notmatch'}, 'Galaxy Evolution Explorer': {'mission': 'Galaxy Evolution Explorer', 'class': 'z_notmatch'}, 'K2': {'mission': 'K2', 'class': 'z_notmatch'}, 'Hubble Legacy Archive': {'mission': 'Hubble Legacy Archive', 'class': 'z_notmatch'}}
Start of text:
1 Introduction Jupiter exhibits the strongest magnetospheric activity in the solar system. The Jovian magnetosphere, ionosphere, and thermosphere (MIT) are coupled electromagnetically, and strong auroral emission is consistently observed as a result. The MIT coupling current system, which flows 

Entry 7284:
ID: 7284
Bibcode: 2022ApJ...926..226M
Missions: {'Hubble': {'mission': 'Hubble', 'class': 'z_notmatch'}, 'Webb Telescope': {'mission': 'Webb Telescope', 'class': 'MENTION'}, 'Transiting Exoplanet Survey Satellite': {'mission': 'Transiting Exoplanet Survey Satellite', 'class': 'z_notmatch'}, 'Kepler': {'mission': 'Kepler', 'class': 'z_notmatch'}, 'Pan-STARRS': {'mission': 'Pan-STARRS', 'class': 'z_notmatch'}, 'Galaxy Evolution Explorer': {'mission': 'Galaxy Evolution Explorer', 'class': 'z_notmatch'}, 'K2': {'mission': 'K2', 'class': 'z_notmatch'}, 'Hubble Legacy Archive': {'mission': 'Hubble Legacy Archive', 'class': 'z_notmatch'}}
Start of text:
1. Introduction Atmospheric escape is one of the key physical processes governing the evolution of planets and planetary atmospheres, especially in the case of exoplanets orbiting at close orbital distances from their host stars (Owen 2019 ). Atmospheric mass loss has been proposed as a possible explanation for the observed lack of


Entry 29280:
ID: 29280
Bibcode: 2019RAA....19...27G
Missions: {'Hubble': {'mission': 'Hubble', 'class': 'z_notmatch'}, 'Webb Telescope': {'mission': 'Webb Telescope', 'class': 'z_notmatch'}, 'Transiting Exoplanet Survey Satellite': {'mission': 'Transiting Exoplanet Survey Satellite', 'class': 'z_notmatch'}, 'Kepler': {'mission': 'Kepler', 'class': 'z_notmatch'}, 'Pan-STARRS': {'mission': 'Pan-STARRS', 'class': 'z_notmatch'}, 'Galaxy Evolution Explorer': {'mission': 'Galaxy Evolution Explorer', 'class': 'MENTION'}, 'K2': {'mission': 'K2', 'class': 'z_notmatch'}, 'Hubble Legacy Archive': {'mission': 'Hubble Legacy Archive', 'class': 'z_notmatch'}}
Start of text:
1 Introduction A bimodal distribution of optical color (Strateva et al. 2001 ; Blanton et al. 2003 ), ultraviolet (UV)-optical color (Salim et al. 2007 ), morphology (Driver et al. 2006 ) or star formation rate (SFR) (Kauffmann et al. 2003a , b ) of galaxies has been unambiguously observed. In color-magnitude diagrams (CMDs), th

-

Entry 3054:
ID: 3054
Bibcode: 2022NatAs...6..659B
Missions: {'Hubble': {'mission': 'Hubble', 'class': 'z_notmatch'}, 'Webb Telescope': {'mission': 'Webb Telescope', 'class': 'z_notmatch'}, 'Transiting Exoplanet Survey Satellite': {'mission': 'Transiting Exoplanet Survey Satellite', 'class': 'z_notmatch'}, 'Kepler': {'mission': 'Kepler', 'class': 'z_notmatch'}, 'Pan-STARRS': {'mission': 'Pan-STARRS', 'class': 'z_notmatch'}, 'Galaxy Evolution Explorer': {'mission': 'Galaxy Evolution Explorer', 'class': 'z_notmatch'}, 'K2': {'mission': 'K2', 'class': 'z_notmatch'}, 'Hubble Legacy Archive': {'mission': 'Hubble Legacy Archive', 'class': 'z_notmatch'}}
Start of text:
Main Studies of the galaxy luminosity function indicate that most of the galaxies in the Universe are dwarfs; that is systems at least one order of magnitude less luminous than the Milky Way (MW). This finding, combined with the fact that, according to the standard cosmological model, structure formation occurs bottom-up (sma

1. Introduction Ultraluminous X-ray sources (ULXs) are defined as point-like off-nuclear X-ray sources with luminosities exceeding 10 39 erg s −1 (for a recent review see Kaaret et al. 2017 ). Therefore, they are the brightest X-ray sources that are neither supernovae (SNe) nor active galactic nuclei. After their identification at the end of the previous century, it was thought for a long time that ULXs contain intermediate-mass ( M ∼ 10 2 –10 4 M ⊙ ) black holes (IMBHs Colbert Mushotzky 1999 ) 
-

Entry 24806:
ID: 24806
Bibcode: 2020ApJ...888...87M
Missions: {'Hubble': {'mission': 'Hubble', 'class': 'z_notmatch'}, 'Webb Telescope': {'mission': 'Webb Telescope', 'class': 'MENTION'}, 'Transiting Exoplanet Survey Satellite': {'mission': 'Transiting Exoplanet Survey Satellite', 'class': 'z_notmatch'}, 'Kepler': {'mission': 'Kepler', 'class': 'z_notmatch'}, 'Pan-STARRS': {'mission': 'Pan-STARRS', 'class': 'z_notmatch'}, 'Galaxy Evolution Explorer': {'mission': 'Galaxy Evolution Explorer', 

Start of text:
1 Introduction Planets similar to Earth but slightly more irradiated are expected to experience a runaway greenhouse transition, a state in which a net positive feedback between surface temperature, evaporation, and atmospheric opacity causes a runaway warming ( Ingersoll 1969 ; Goldblatt Watson 2012 ). This runaway greenhouse positive feedback ceases only when oceans have completely boiled away, forming an optically thick H 2 O-dominated atmosphere. Venus may have experienced a runaway greenhou
-

Entry 13611:
ID: 13611
Bibcode: 2021MNRAS.502.1487J
Missions: {'Hubble': {'mission': 'Hubble', 'class': 'z_notmatch'}, 'Webb Telescope': {'mission': 'Webb Telescope', 'class': 'z_notmatch'}, 'Transiting Exoplanet Survey Satellite': {'mission': 'Transiting Exoplanet Survey Satellite', 'class': 'z_notmatch'}, 'Kepler': {'mission': 'Kepler', 'class': 'z_notmatch'}, 'Pan-STARRS': {'mission': 'Pan-STARRS', 'class': 'MENTION'}, 'Galaxy Evolution Explorer': {'mission': 'Galaxy Evolut

Bibcode: 2019ApJ...874...18W
Missions: {'Hubble': {'mission': 'Hubble', 'class': 'SCIENCE'}, 'Webb Telescope': {'mission': 'Webb Telescope', 'class': 'z_notmatch'}, 'Transiting Exoplanet Survey Satellite': {'mission': 'Transiting Exoplanet Survey Satellite', 'class': 'z_notmatch'}, 'Kepler': {'mission': 'Kepler', 'class': 'z_notmatch'}, 'Pan-STARRS': {'mission': 'Pan-STARRS', 'class': 'z_notmatch'}, 'Galaxy Evolution Explorer': {'mission': 'Galaxy Evolution Explorer', 'class': 'z_notmatch'}, 'K2': {'mission': 'K2', 'class': 'z_notmatch'}, 'Hubble Legacy Archive': {'mission': 'Hubble Legacy Archive', 'class': 'z_notmatch'}}
Start of text:
1. Introduction Galaxies grow in mass through a combination of mergers with other galaxies and smooth accretion of baryons and dark matter. Predicting the frequency of both major (i.e., with roughly equal masses) and minor (i.e., with significantly unequal masses) mergers as a function of galaxy mass and redshift is therefore an important component of 

1. Introduction Massive stars profoundly influence the evolution of the universe, from galactic dynamics and structure to star formation. They are often found with bound companions. Massive stars have a higher frequency of multiplicity than cooler, less massive stars (Raghavan et al. 2010 ; Duchêne Kraus 2013 ), especially when they are found in clusters (Mason et al. 2009 ). Spectroscopic studies of massive stars in the Milky Way (Sana et al. 2012 ) and in the Tarantula Nebula region of the Lar
-

Entry 47398:
ID: 47398
Bibcode: 2017MNRAS.467..102C
Missions: {'Hubble': {'mission': 'Hubble', 'class': 'z_notmatch'}, 'Webb Telescope': {'mission': 'Webb Telescope', 'class': 'z_notmatch'}, 'Transiting Exoplanet Survey Satellite': {'mission': 'Transiting Exoplanet Survey Satellite', 'class': 'z_notmatch'}, 'Kepler': {'mission': 'Kepler', 'class': 'z_notmatch'}, 'Pan-STARRS': {'mission': 'Pan-STARRS', 'class': 'z_notmatch'}, 'Galaxy Evolution Explorer': {'mission': 'Galaxy Evolution Explorer

1. Introduction Star formation is a key component of the formation and evolution of galaxies. Galaxy star formation histories (SFHs) bear imprints of the various physical processes that regulate their star formation across a broad range of timescales. Some examples of these processes and their relevant timescales include supermassive black hole feedback (Anglés-Alcázar et al. 2017 ; ≳1 Gyr), inflows and outflows of gas (Pillepich et al. 2017 ; Weinberger et al. 2017 ; 100–500 Myr), galaxy merger
-

Entry 48084:
ID: 48084
Bibcode: 2017ApJ...839...16C
Missions: {'Hubble': {'mission': 'Hubble', 'class': 'z_notmatch'}, 'Webb Telescope': {'mission': 'Webb Telescope', 'class': 'z_notmatch'}, 'Transiting Exoplanet Survey Satellite': {'mission': 'Transiting Exoplanet Survey Satellite', 'class': 'z_notmatch'}, 'Kepler': {'mission': 'Kepler', 'class': 'MENTION'}, 'Pan-STARRS': {'mission': 'Pan-STARRS', 'class': 'z_notmatch'}, 'Galaxy Evolution Explorer': {'mission': 'Galaxy Evolution Explorer', 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [10]:
#For use of fake, made-up data entries to test on
if (not do_real_testdata):
    print("Using fake test data for testing.")
    #Make some fake data
    dict_texts_raw = {"science":["We present HST observations in Figure 4.",
                        "The HST stars are listed in Table 3b.",
                        "Despite our efforts to smooth the data, there are still rings in the HST images.",
                        "See Section 8c for more discussion of the Hubble images.",
                        "The supernovae detected with HST tend to be brighter than initially predicted.",
                        "Our spectra from HST fit well to the standard trend first published in Someone et al. 1990.",
                        "We use the Hubble Space Telescope to build an ultraviolet database of the target stars.",
                        "The blue points (HST) exhibit more scatter than the red points (JWST).",
                        "The benefit, then, is the far higher S/N we achieved in our HST observations.",
                        "Here we employ the Hubble Telescope to observe the edge of the photon-dominated region.",
                        "The black line shows that the region targeted with Hubble has an extreme UV signature."],
                 "datainfluenced":["The simulated Hubble data is plotted in Figure 4.",
                       "Compared to the HST observations in Someone et al., our JWST follow-up reached higher S/N.",
                       "We were able to reproduce the luminosities from Hubble using our latest models.",
                       "We overplot Hubble-observed stars from Someone et al. in Figure 3b.",
                       "We built the spectral templates using UV data in the Hubble archive.",
                       "We simulate what our future HST observations will look like to predict the S/N.",
                       "Our work here with JWST is inspired by our earlier HST study published in 2010.",
                       "We therefore use the Hubble statistics from Author et al. to guide our stellar predictions.",
                       "The stars in Figure 3 were plotted based on the HST-fitted trend line in Person et al.",
                       "The final step is to use the HST exposure tool to put our modeled images in context."],
                 "mention":["Person et al. used HST to measure the Hubble constant.",
                        "We will present new HST observations in a future work.",
                        "HST is a fantastic instrument that has revolutionized our view of space.",
                        "The Hubble Space Telescope (HST) has its mission center at the STScI.",
                        "We can use HST to power a variety of science in the ultraviolet regime.",
                        "It is not clear when the star will be observable with HST.",
                        "More data can be found and downloaded from the Hubble archive.",
                        "We note that HST can be used to observe the stars as well, at higher S/N.",
                        "However, we ended up using the JWST rather than HST observations in this work.",
                        "We push the analysis of the Hubble component of the dataset to a future study.",
                        "We expect the HST observations to be released in the fall.",
                        "We look forward to any follow-up studies with, e.g., the Hubble Telescope."]}
    #
    #Convert into dictionary with: key:text,class,id,mission structure
    i_track = 0
    dict_texts = {}
    #Store subheadings by mission, to avoid duplicating and processing the same text across different missions
    mission = operator_1._fetch_keyword_object(lookup="HST")._get_info("name")
    for key in dict_texts_raw:
        curr_set = dict_texts_raw[key]
        for ii in range(0, len(curr_set)):
            dict_texts[str(i_track)] = {"text":curr_set[ii], "id":"{0}_{1}".format(key, ii), "bibcode":str(i_track),
                                        "missions":{mission:{"mission":mission, "class":key}}}
            i_track += 1
    #
    print("Mission: {0}".format(mission))
    print("Number of texts in text set: {0}".format(len(dict_texts)))
    print("")
    for key in dict_texts:
        print(dict_texts[key])
        print("-")
    #
#

Next, let's prepare some additional information for each of these classifiers.  We'll need to set, for example, the uncertainty thresholds for accepting or rejecting each classifier's output.

In [11]:
#Store texts for each operator and its internal classifier
#For operator 1
dict_texts_1 = dict_texts #Dictionary of texts to classify

#For operator 2
dict_texts_2 = dict_texts #Dictionary of texts to classify

#Gather into list
list_dict_texts = [dict_texts_1, dict_texts_2]

Now, let's evaluate the performance of these classifiers in different ways.  We will consider these performance tests:
* Basic: We generate confusion matrices for the set of Operators (containing the different classifiers).
* Uncertainty: We plot performance as a function of uncertainty level for the set of Operators.

In [12]:
#Create an instance of the Performance class
performer = bibcat.Performance()

The Basic evaluation:

In [13]:
#Parameters for this evaluation
fileroot_evaluation = "test_eval_basic" #Root name of the file within which to store the performance evaluation output
fileroot_misclassif = "test_misclassif_basic" #Root name of the file within which to store misclassified text information
figsize = (20, 12)

#Run the pipeline for a basic evaluation of model performance
performer.evaluate_performance_basic(operators=list_operators, dicts_texts=list_dict_texts, mappers=list_mappers,
                                     thresholds=list_thresholds, buffers=list_buffers, is_text_processed=False,
                                     do_reuse_run=do_reuse_run,
                                     do_verify_truematch=do_verify_truematch, do_raise_innererror=do_raise_innererror,
                                     do_save_evaluation=True, do_save_misclassif=True, filepath_output=filepath_output,
                                     fileroot_evaluation=fileroot_evaluation, fileroot_misclassif=fileroot_misclassif,
                                     print_freq=1, do_verbose=True, do_verbose_deep=False, figsize=figsize)


> Running evaluate_performance_basic()!
Generating evaluation for the given operators...

> Running _generate_evaluation()!
Iterating through Operators to classify each set of text...
Classifying with Operator #0...

> Running classify_set()!
Classification for text #1 of 4632 complete...
Classification for text #2 of 4632 complete...
-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecognized ambig. phrase:\nHubble time\nTaken from this text snippet:\nIn this model, the cloud (and cluster) truncation masses correlate with gas pressure, so the highest pressure environments are more likely to form massive stellar clusters that can survive for a Hubble time.')
Error was noted. Returning error as verdict.
-
Classification for text #3 of 4632 complete...
Classification for text #4 of 4632 complete...
Classification for text #5 of 4632 complete...
-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecognized ambig. phrase:\nHubble ’s re

-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecognized ambig. phrase:\nspectral type F6 - K2\nTaken from this text snippet:\nMoreover, the color excess E (H − W 000 is calculated by assuming that the intrinsic color index (H − W 000 000 is a constant of 000.000 for Cepheids mainly of spectral type F6-K2 as demonstrated by Authorsetal.')
Error was noted. Returning error as verdict.
-
Classification for text #60 of 4632 complete...
Classification for text #61 of 4632 complete...
Classification for text #62 of 4632 complete...
Classification for text #63 of 4632 complete...
Classification for text #64 of 4632 complete...
Classification for text #65 of 4632 complete...
-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecognized ambig. phrase:\nDN comet C/000 K2\nTaken from this text snippet:\nWhether this result that DN comets produce more CO 000 than CO at perihelion holds for all Oort Cloud comets can be tested this year with t

-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecognized ambig. phrase:\nK2 GAP\nTaken from this text snippet:\nBased on the photometric data obtained from the K2 Galactic Archaeology Program (K2 GAP, Stelloetal 000, 000, Authorsetal analyzed the ages of red giant stars from two campaign fields C3 and C6 of K2 GAP and found a clear bimodality in the age distributions for both the Kepler and the K2 fields, with distinct young and old age at 000 and 000 Gyr for a sample of red giants with age uncertainties 000% (in their Figure 000.')
Error was noted. Returning error as verdict.
-
Classification for text #125 of 4632 complete...
Classification for text #126 of 4632 complete...
Classification for text #127 of 4632 complete...
Classification for text #128 of 4632 complete...
Classification for text #129 of 4632 complete...
Classification for text #130 of 4632 complete...
-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecognized a

Classification for text #188 of 4632 complete...
Classification for text #189 of 4632 complete...
Classification for text #190 of 4632 complete...
Classification for text #191 of 4632 complete...
Classification for text #192 of 4632 complete...
Classification for text #193 of 4632 complete...
Classification for text #194 of 4632 complete...
-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecognized ambig. phrase:\ntheoretical Hubble diagram\nTaken from this text snippet:\nThe most straightforward technique to constrain the cosmic curvature is by confronting the theoretical Hubble diagram (reconstructed by the Hubble parameter measurements) with the observed luminosity distances to the objects whose redshifts are known.')
Error was noted. Returning error as verdict.
-
Classification for text #195 of 4632 complete...
Classification for text #196 of 4632 complete...
Classification for text #197 of 4632 complete...
Classification for text #198 of 4632 complete.

Classification for text #279 of 4632 complete...
Classification for text #280 of 4632 complete...
Classification for text #281 of 4632 complete...
Classification for text #282 of 4632 complete...
Classification for text #283 of 4632 complete...
Classification for text #284 of 4632 complete...
-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecognized ambig. phrase:\nHubble time\nTaken from this text snippet:\nThis process is more gradual, so that the total mass loss reaches ≈000% only after ≈000 Gyr and does not reach 000% until ages on the order of a Hubble time.')
Error was noted. Returning error as verdict.
-
Classification for text #285 of 4632 complete...
-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecognized ambig. phrase:\nHubble parameter\nTaken from this text snippet:\nCMB photons scatter off a fraction τ es of free electrons created during reionization, suppressing CMB anisotropies by exp (−τ es), below angular sca

...

Classification for text #4428 of 4632 complete...
Classification for text #4429 of 4632 complete...
Classification for text #4430 of 4632 complete...
Classification for text #4431 of 4632 complete...
Classification for text #4432 of 4632 complete...
Classification for text #4433 of 4632 complete...
-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecognized ambig. phrase:\nKepler ’s laws\nTaken from this text snippet:\nThe velocities of the eclipsing bodies are related to their orbital separation via Kepler’s laws, with a = GM / 000.')
Error was noted. Returning error as verdict.
-
Classification for text #4434 of 4632 complete...
Classification for text #4435 of 4632 complete...
Classification for text #4436 of 4632 complete...
Classification for text #4437 of 4632 complete...
Classification for text #4438 of 4632 complete...
Classification for text #4439 of 4632 complete...
-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecogn

Classification for text #4508 of 4632 complete...
Classification for text #4509 of 4632 complete...
Classification for text #4510 of 4632 complete...
Classification for text #4511 of 4632 complete...
-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecognized ambig. phrase:\nparticular Kepler\nTaken from this text snippet:\nHowever, over the last few years, an increasing number of results have been obtained using photometric data, in particular Kepler, using the short-term variability indicator R per (or equivalent measurements).')
Error was noted. Returning error as verdict.
-
Classification for text #4512 of 4632 complete...
Classification for text #4513 of 4632 complete...
Classification for text #4514 of 4632 complete...
Classification for text #4515 of 4632 complete...
Classification for text #4516 of 4632 complete...
Classification for text #4517 of 4632 complete...
Classification for text #4518 of 4632 complete...
Classification for text #4519 of 4632

Classification for text #4532 of 4632 complete...
-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecognized ambig. phrase:\nKepler detector\nTaken from this text snippet:\nThe absolute sensitivity of the Kepler detector pixels decays at approximately 000% yr −000, due to sudden pixel sensitivity dropouts and other environmental lifetime factors.')
Error was noted. Returning error as verdict.
-
-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecognized ambig. phrase:\nK2 long - cadence\nTaken from this text snippet:\nJoint Modeling of ASAS-SN and K2 Light Curves We attempt to unify the ASAS-SN, K2 long-cadence, and K2 FFI data points into a single global light curve.')
Error was noted. Returning error as verdict.
-
Classification for text #4533 of 4632 complete...
Classification for text #4534 of 4632 complete...
Classification for text #4535 of 4632 complete...
Classification for text #4536 of 4632 complete...
Classification fo

Classification for text #4594 of 4632 complete...
Classification for text #4595 of 4632 complete...
Classification for text #4596 of 4632 complete...
Classification for text #4597 of 4632 complete...
Classification for text #4598 of 4632 complete...
Classification for text #4599 of 4632 complete...
Classification for text #4600 of 4632 complete...
Classification for text #4601 of 4632 complete...
Classification for text #4602 of 4632 complete...
Classification for text #4603 of 4632 complete...
Classification for text #4604 of 4632 complete...
Classification for text #4605 of 4632 complete...
Classification for text #4606 of 4632 complete...
Classification for text #4607 of 4632 complete...
Classification for text #4608 of 4632 complete...
-
The following err. was encountered in operate:
NotImplementedError('Err: Unrecognized ambig. phrase:\nHubble flow\nTaken from this text snippet:\nAssuming that the structure is just breaking away from the Hubble flow, and following Authorsetal, C c


Evaluation saved at: /Users/jamila.pegues/Documents/STScI_Fellowship/Functional/Library/BibTracking/repo_stsci/bibcat/src/models/run_class2_full_none_uniform/output/test_eval_basic.npy

Run of _generate_evaluation() complete!

Evaluations generated.
Plotting confusion matrices...

> Running _combine_performance_across_evaluations()!
Combining evaluations across these operators: ['Operator_ML', 'Operator_RB']
All possible operator combinations: [('Operator_ML', 'Operator_RB')]
Considering combination: ('Operator_ML', 'Operator_RB')
Run of _combine_performance_across_evaluations() complete!
Confusion matrices have been plotted at:
/Users/jamila.pegues/Documents/STScI_Fellowship/Functional/Library/BibTracking/repo_stsci/bibcat/src/models/run_class2_full_none_uniform/output

Run of evaluate_performance_basic() complete!


The Uncertainty evaluation:

In [14]:
print(temporaryblockforerror)
woo = temporaryblock * 3

NameError: name 'temporaryblockforerror' is not defined

In [ ]:
#Parameters for this evaluation
fileroot_evaluation = "test_eval_uncertainty" #Root name of the file within which to store the performance evaluation output
fileroot_misclassif = "test_misclassif_uncertainty" #Root name of the file within which to store misclassified text information
figsize = (40, 12)

#Run the pipeline for an evaluation of model performance as a function of uncertainty
performer.evaluate_performance_uncertainty(operators=list_operators, dicts_texts=list_dict_texts, mappers=list_mappers,
                                     threshold_arrays=list_threshold_arrays, buffers=list_buffers,
                                     is_text_processed=False, do_reuse_run=do_reuse_run,
                                     do_verify_truematch=do_verify_truematch, do_raise_innererror=do_raise_innererror,
                                     do_save_evaluation=True, do_save_misclassif=True, filepath_output=filepath_output,
                                     fileroot_evaluation=fileroot_evaluation, fileroot_misclassif=fileroot_misclassif,
                                     print_freq=25, do_verbose=True, do_verbose_deep=False, figsize=figsize)

And with that, you should have new confusion matrices summarizing the basic performance for these classifiers saved in your requested directory!

---

In [ ]:
#Set end marker for this tutorial.
print("This tutorial completed successfully.")